In [61]:
# tensorflow imports
from tensorflow.keras.layers import Conv2D, BatchNormalization, Dropout, MaxPooling2D, Dense, Input, Activation, AveragePooling2D, Flatten, ZeroPadding2D
from tensorflow.keras.layers import Conv1D, MaxPooling1D, GlobalAvgPool1D, AveragePooling1D
from tensorflow.keras.models import Model
from tensorflow.keras.initializers import RandomNormal, GlorotNormal, he_normal
from tensorflow.keras.utils import plot_model
from scipy.ndimage.interpolation import rotate
from scipy import signal
from tensorflow.keras.callbacks import ModelCheckpoint
from tensorflow.keras.callbacks import EarlyStopping
import tensorflow as tf
from tensorflow.keras import models, layers
from tensorflow.keras.optimizers import RMSprop
from tensorflow.keras.preprocessing import image
from tensorflow.keras.callbacks import CSVLogger
import random

from tqdm import tqdm
import numpy as np
import os
import pywt
from matplotlib import pyplot as plt
from pywt._doc_utils import wavedec2_keys, draw_2d_wp_basis
import datetime
import warnings
warnings.filterwarnings("ignore")
import cv2

import time
import concurrent.futures

In [3]:
# tensorflow model
Inp = Input(shape = (1050, 1))
x = Conv1D(1, 7,kernel_initializer=he_normal(seed=20), name='conv1')(Inp)
x = BatchNormalization()(x)
x = Activation('relu')(x)
x = MaxPooling1D((2), strides=2)(x)

x = Conv1D(1, 3, kernel_initializer=he_normal(seed=20), name='conv2')(x)
x = BatchNormalization()(x)
x = Activation('relu')(x)
x = MaxPooling1D(2)(x)

x = Flatten()(x)
x = Dense(256, activation='relu',kernel_initializer=he_normal(seed=20))(x)
out = Dense(1, activation = 'sigmoid',kernel_initializer=he_normal(seed=20), name = 'ouput')(x)

model = Model(inputs = Inp, outputs = out)
model.summary()

Model: "model_1"
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
input_2 (InputLayer)         [(None, 1050, 1)]         0         
_________________________________________________________________
conv1 (Conv1D)               (None, 1044, 1)           8         
_________________________________________________________________
batch_normalization_2 (Batch (None, 1044, 1)           4         
_________________________________________________________________
activation_2 (Activation)    (None, 1044, 1)           0         
_________________________________________________________________
max_pooling1d_2 (MaxPooling1 (None, 522, 1)            0         
_________________________________________________________________
conv2 (Conv1D)               (None, 520, 1)            4         
_________________________________________________________________
batch_normalization_3 (Batch (None, 520, 1)            4   

In [4]:
def DDWT(img, level: int, wavelet: str):
    c = pywt.wavedec2(img, wavelet=wavelet, level = level)
  # normalize each coefficient array independently for better visibility
  # c[0] /= np.abs(c[0]).max()
    return c

In [5]:
def get_avg_of_array(array):
    return array.mean()

def get_var_of_array(array):
    return np.var(array)

def get_energy_in_array(array):
    return np.sum(np.square(array))


def get_entropy_in_array(array):
    return -np.sum(np.multiply(array,np.log(array)))

def get_sharpness_in_subband(array):
    con = 0
    for i in range(array.shape[0]):
        for j in range(array.shape[1]):
            con += ((i - j)**2) * array[i][j]
    return con

def get_degree_change(array):
    Im = 0
    for i in range(array.shape[0]):
        for j in range(array.shape[1]):
            if ( i != j):
                Im += array[i][j] / abs(i - j)
    return Im

def get_homoginity(array):
    Idm = 0
    for i in range(array.shape[0]):
        for j in range(array.shape[1]):
            Idm += array[i][j] / ( 1 + ( i - j )**2)
    return Idm

In [53]:
def extract_features(array):
    start_time = time.time()
    mean = get_avg_of_array(array)
    print("--- %s mean seconds ---" % (time.time() - start_time))
    start_time = time.time()
    var = get_var_of_array(array)
    print("--- %s var seconds ---" % (time.time() - start_time))
    start_time = time.time()
    energy = get_energy_in_array(array)
    print("--- %s energy seconds ---" % (time.time() - start_time))
    start_time = time.time()
    entropy = get_entropy_in_array(array)
    print("--- %s entropy seconds ---" % (time.time() - start_time))
    start_time = time.time()
    sharpness = get_sharpness_in_subband(array)
    print("--- %s sharpness seconds ---" % (time.time() - start_time))
    start_time = time.time()
    degree = get_degree_change(array)
    print("--- %s degree seconds ---" % (time.time() - start_time))
    start_time = time.time()
    homoginity = get_homoginity(array)
    print("--- %s homoginity seconds ---" % (time.time() - start_time))
    return [mean, var, energy, entropy, sharpness, degree, homoginity]

In [57]:
def get_features(img, level, wavelet):
    #img = cv2.imread(path)
    features = list()
    # wavelet transform
    start_time = time.time()
    c = DDWT(img, level, wavelet)
    print("--- %s DWT seconds ---" % (time.time() - start_time))
    features.extend(extract_features(c[0]))

    
    for i in range(1, len(c)):
        for j in range(level):
            features.extend(extract_features(c[i][j]))
    print("--- %s total extraction per wavelet seconds ---" % (time.time() - start_time))
#print(len(features))

    return features


In [43]:
def get_features_for_image(image):
    wavelets = ['db1', 'db2', 'db3', 'db4', 'db5']
    features = list()
  # img = cv2.imread(path)
    img = image
    for i in range(img.shape[2]):
        for j in wavelets:
            features.extend(get_features(img[:,:, i], 3, j))
    return np.array(features).reshape(1050,1)

In [11]:
model.compile(optimizer='adam', loss='binary_crossentropy', metrics=['accuracy'])
# log_dir = "logs2/fit/" + datetime.datetime.now().strftime("%Y%m%d-%H%M%S")
# filepath = './models/model-FCNN-Relu.h5';
# checkpoint = ModelCheckpoint(filepath, monitor='val_loss', verbose=1, save_best_only=True, mode='min')
# tensorboard_callback = tf.keras.callbacks.TensorBoard(log_dir=log_dir, histogram_freq=1, write_images=True)

In [19]:
def data_shuffle(data_path):
  # Identify the number of classes in the given directory.
    classes = sorted(os.listdir(data_path))
  #print(classes)
    no_of_classes = len(classes)
    img_array = list()
  # generate path and label array for the images in all classes
    tmp_class = 0
    for i in classes:
        for j in os.listdir(data_path + i):
            img_array.append([data_path + i + '/' + j, tmp_class])
        tmp_class += 1
    random.shuffle(img_array)
    print('{} images found in {} classes'.format(len(img_array), no_of_classes))
    return img_array

In [32]:
def custom_data_gen_train(path, batch_size = 64):
  # get shuffled img paths and labels
    print(path)
    samples = data_shuffle(path)
    num_samples = len(samples)
    # while loop so that generators never terminates
    while True:
        for offset in range(0, num_samples, batch_size):
            # Get the samples you'll use in this batch
            batch_samples = samples[offset:offset+batch_size]

            #x and y for this batch
            x_train = []
            y_train = []

            for batch_sample in batch_samples:
                fileName = batch_sample[0]
                label = batch_sample[1]
                image = cv2.imread(fileName)
                features = get_features_for_image(image)
                x_train.append(features)
                y_train.append(label)
        
            yield np.array(x_train), np.array(y_train)


In [58]:
train_datagen = custom_data_gen_train('../input/patches/train/')
validation_datagen = custom_data_gen_train('../input/patches/validation/')

In [59]:
import time
start_time = time.time()
train_data = next(train_datagen)
print("--- %s seconds ---" % (time.time() - start_time))

../input/patches/train/
3751091 images found in 2 classes
--- 0.0 DWT seconds ---
--- 0.0 mean seconds ---
--- 0.0 var seconds ---
--- 0.0 energy seconds ---
--- 0.0 entropy seconds ---
--- 0.0 sharpness seconds ---
--- 0.0 degree seconds ---
--- 0.0 homoginity seconds ---
--- 0.0 mean seconds ---
--- 0.0 var seconds ---
--- 0.0 energy seconds ---
--- 0.0 entropy seconds ---
--- 0.0 sharpness seconds ---
--- 0.0 degree seconds ---
--- 0.0 homoginity seconds ---
--- 0.0 mean seconds ---
--- 0.0 var seconds ---
--- 0.0 energy seconds ---
--- 0.0 entropy seconds ---
--- 0.0 sharpness seconds ---
--- 0.0 degree seconds ---
--- 0.0 homoginity seconds ---
--- 0.0 mean seconds ---
--- 0.0 var seconds ---
--- 0.0 energy seconds ---
--- 0.0 entropy seconds ---
--- 0.0 sharpness seconds ---
--- 0.0009963512420654297 degree seconds ---
--- 0.0 homoginity seconds ---
--- 0.0 mean seconds ---
--- 0.0 var seconds ---
--- 0.0 energy seconds ---
--- 0.0 entropy seconds ---
--- 0.0 sharpness seconds --

--- 0.0 homoginity seconds ---
--- 0.0 mean seconds ---
--- 0.0 var seconds ---
--- 0.0 energy seconds ---
--- 0.0 entropy seconds ---
--- 0.0 sharpness seconds ---
--- 0.0 degree seconds ---
--- 0.0009970664978027344 homoginity seconds ---
--- 0.0 mean seconds ---
--- 0.0 var seconds ---
--- 0.0 energy seconds ---
--- 0.0 entropy seconds ---
--- 0.0 sharpness seconds ---
--- 0.0 degree seconds ---
--- 0.0009975433349609375 homoginity seconds ---
--- 0.0 mean seconds ---
--- 0.0 var seconds ---
--- 0.0 energy seconds ---
--- 0.0 entropy seconds ---
--- 0.000997304916381836 sharpness seconds ---
--- 0.0 degree seconds ---
--- 0.000997304916381836 homoginity seconds ---
--- 0.0 mean seconds ---
--- 0.000997304916381836 var seconds ---
--- 0.0 energy seconds ---
--- 0.0 entropy seconds ---
--- 0.0009970664978027344 sharpness seconds ---
--- 0.0 degree seconds ---
--- 0.000997304916381836 homoginity seconds ---
--- 0.0 mean seconds ---
--- 0.0 var seconds ---
--- 0.0 energy seconds ---
---

--- 0.0009970664978027344 DWT seconds ---
--- 0.0 mean seconds ---
--- 0.0 var seconds ---
--- 0.0 energy seconds ---
--- 0.0 entropy seconds ---
--- 0.0 sharpness seconds ---
--- 0.000997304916381836 degree seconds ---
--- 0.0 homoginity seconds ---
--- 0.0 mean seconds ---
--- 0.0 var seconds ---
--- 0.0 energy seconds ---
--- 0.0 entropy seconds ---
--- 0.0 sharpness seconds ---
--- 0.0 degree seconds ---
--- 0.0 homoginity seconds ---
--- 0.0 mean seconds ---
--- 0.0 var seconds ---
--- 0.0 energy seconds ---
--- 0.0009975433349609375 entropy seconds ---
--- 0.0 sharpness seconds ---
--- 0.0 degree seconds ---
--- 0.0 homoginity seconds ---
--- 0.0 mean seconds ---
--- 0.0 var seconds ---
--- 0.0 energy seconds ---
--- 0.0 entropy seconds ---
--- 0.0 sharpness seconds ---
--- 0.0009970664978027344 degree seconds ---
--- 0.0 homoginity seconds ---
--- 0.0 mean seconds ---
--- 0.0 var seconds ---
--- 0.0 energy seconds ---
--- 0.0 entropy seconds ---
--- 0.0 sharpness seconds ---
---

--- 0.0 var seconds ---
--- 0.0 energy seconds ---
--- 0.0 entropy seconds ---
--- 0.0 sharpness seconds ---
--- 0.0 degree seconds ---
--- 0.0009965896606445312 homoginity seconds ---
--- 0.0 mean seconds ---
--- 0.0 var seconds ---
--- 0.0 energy seconds ---
--- 0.0 entropy seconds ---
--- 0.0 sharpness seconds ---
--- 0.0 degree seconds ---
--- 0.0 homoginity seconds ---
--- 0.0 mean seconds ---
--- 0.0 var seconds ---
--- 0.0 energy seconds ---
--- 0.0009975433349609375 entropy seconds ---
--- 0.0 sharpness seconds ---
--- 0.0 degree seconds ---
--- 0.0 homoginity seconds ---
--- 0.0 mean seconds ---
--- 0.0 var seconds ---
--- 0.0 energy seconds ---
--- 0.0 entropy seconds ---
--- 0.0009970664978027344 sharpness seconds ---
--- 0.0009975433349609375 degree seconds ---
--- 0.0009970664978027344 homoginity seconds ---
--- 0.0 mean seconds ---
--- 0.0 var seconds ---
--- 0.0 energy seconds ---
--- 0.0 entropy seconds ---
--- 0.0009975433349609375 sharpness seconds ---
--- 0.0 degree 

--- 0.000997304916381836 homoginity seconds ---
--- 0.013962745666503906 total extraction per wavelet seconds ---
--- 0.001995086669921875 DWT seconds ---
--- 0.0 mean seconds ---
--- 0.0 var seconds ---
--- 0.0 energy seconds ---
--- 0.0 entropy seconds ---
--- 0.0 sharpness seconds ---
--- 0.0 degree seconds ---
--- 0.0 homoginity seconds ---
--- 0.0 mean seconds ---
--- 0.0 var seconds ---
--- 0.0 energy seconds ---
--- 0.0 entropy seconds ---
--- 0.0 sharpness seconds ---
--- 0.0 degree seconds ---
--- 0.0 homoginity seconds ---
--- 0.0 mean seconds ---
--- 0.0 var seconds ---
--- 0.0 energy seconds ---
--- 0.0 entropy seconds ---
--- 0.0 sharpness seconds ---
--- 0.0 degree seconds ---
--- 0.0 homoginity seconds ---
--- 0.0 mean seconds ---
--- 0.0 var seconds ---
--- 0.0 energy seconds ---
--- 0.0 entropy seconds ---
--- 0.0 sharpness seconds ---
--- 0.0 degree seconds ---
--- 0.0 homoginity seconds ---
--- 0.0 mean seconds ---
--- 0.0 var seconds ---
--- 0.0 energy seconds ---
-

...

--- 0.0009970664978027344 homoginity seconds ---
--- 0.0 mean seconds ---
--- 0.0 var seconds ---
--- 0.0 energy seconds ---
--- 0.0 entropy seconds ---
--- 0.000997781753540039 sharpness seconds ---
--- 0.0009970664978027344 degree seconds ---
--- 0.0009975433349609375 homoginity seconds ---
--- 0.0 mean seconds ---
--- 0.0 var seconds ---
--- 0.0 energy seconds ---
--- 0.0 entropy seconds ---
--- 0.000997304916381836 sharpness seconds ---
--- 0.0009975433349609375 degree seconds ---
--- 0.0009970664978027344 homoginity seconds ---
--- 0.01795196533203125 total extraction per wavelet seconds ---
--- 0.0009968280792236328 DWT seconds ---
--- 0.0 mean seconds ---
--- 0.0 var seconds ---
--- 0.0 energy seconds ---
--- 0.0 entropy seconds ---
--- 0.0 sharpness seconds ---
--- 0.0 degree seconds ---
--- 0.0 homoginity seconds ---
--- 0.0 mean seconds ---
--- 0.0 var seconds ---
--- 0.0 energy seconds ---
--- 0.0 entropy seconds ---
--- 0.000997781753540039 sharpness seconds ---
--- 0.0 deg

--- 0.0009965896606445312 DWT seconds ---
--- 0.0 mean seconds ---
--- 0.0 var seconds ---
--- 0.0 energy seconds ---
--- 0.0 entropy seconds ---
--- 0.0 sharpness seconds ---
--- 0.0 degree seconds ---
--- 0.0 homoginity seconds ---
--- 0.0 mean seconds ---
--- 0.0 var seconds ---
--- 0.0 energy seconds ---
--- 0.0009980201721191406 entropy seconds ---
--- 0.0 sharpness seconds ---
--- 0.0 degree seconds ---
--- 0.0 homoginity seconds ---
--- 0.0 mean seconds ---
--- 0.0 var seconds ---
--- 0.0 energy seconds ---
--- 0.0 entropy seconds ---
--- 0.0 sharpness seconds ---
--- 0.0 degree seconds ---
--- 0.0 homoginity seconds ---
--- 0.0 mean seconds ---
--- 0.0 var seconds ---
--- 0.0 energy seconds ---
--- 0.0 entropy seconds ---
--- 0.0 sharpness seconds ---
--- 0.0 degree seconds ---
--- 0.0009970664978027344 homoginity seconds ---
--- 0.0 mean seconds ---
--- 0.0 var seconds ---
--- 0.0 energy seconds ---
--- 0.0 entropy seconds ---
--- 0.0 sharpness seconds ---
--- 0.0 degree secon

--- 0.000997304916381836 sharpness seconds ---
--- 0.0009975433349609375 degree seconds ---
--- 0.0009975433349609375 homoginity seconds ---
--- 0.01595759391784668 total extraction per wavelet seconds ---
--- 0.0029909610748291016 DWT seconds ---
--- 0.0 mean seconds ---
--- 0.0 var seconds ---
--- 0.0 energy seconds ---
--- 0.0 entropy seconds ---
--- 0.0 sharpness seconds ---
--- 0.0 degree seconds ---
--- 0.0 homoginity seconds ---
--- 0.0 mean seconds ---
--- 0.0 var seconds ---
--- 0.0 energy seconds ---
--- 0.0 entropy seconds ---
--- 0.0009982585906982422 sharpness seconds ---
--- 0.0 degree seconds ---
--- 0.0 homoginity seconds ---
--- 0.0 mean seconds ---
--- 0.0 var seconds ---
--- 0.0 energy seconds ---
--- 0.0 entropy seconds ---
--- 0.0 sharpness seconds ---
--- 0.0 degree seconds ---
--- 0.0009970664978027344 homoginity seconds ---
--- 0.0 mean seconds ---
--- 0.0 var seconds ---
--- 0.0 energy seconds ---
--- 0.0 entropy seconds ---
--- 0.0 sharpness seconds ---
--- 0.

--- 0.0 entropy seconds ---
--- 0.000997304916381836 sharpness seconds ---
--- 0.0 degree seconds ---
--- 0.0 homoginity seconds ---
--- 0.0 mean seconds ---
--- 0.0 var seconds ---
--- 0.0 energy seconds ---
--- 0.0 entropy seconds ---
--- 0.0 sharpness seconds ---
--- 0.0 degree seconds ---
--- 0.0009970664978027344 homoginity seconds ---
--- 0.0 mean seconds ---
--- 0.0 var seconds ---
--- 0.0 energy seconds ---
--- 0.0 entropy seconds ---
--- 0.0 sharpness seconds ---
--- 0.0 degree seconds ---
--- 0.0 homoginity seconds ---
--- 0.0 mean seconds ---
--- 0.0 var seconds ---
--- 0.0 energy seconds ---
--- 0.0 entropy seconds ---
--- 0.000997304916381836 sharpness seconds ---
--- 0.0 degree seconds ---
--- 0.0009975433349609375 homoginity seconds ---
--- 0.0 mean seconds ---
--- 0.0 var seconds ---
--- 0.0 energy seconds ---
--- 0.0 entropy seconds ---
--- 0.0 sharpness seconds ---
--- 0.000997304916381836 degree seconds ---
--- 0.000997304916381836 homoginity seconds ---
--- 0.0 mean

--- 0.0009963512420654297 DWT seconds ---
--- 0.0 mean seconds ---
--- 0.0 var seconds ---
--- 0.0 energy seconds ---
--- 0.0 entropy seconds ---
--- 0.0 sharpness seconds ---
--- 0.0 degree seconds ---
--- 0.0 homoginity seconds ---
--- 0.0 mean seconds ---
--- 0.0 var seconds ---
--- 0.0 energy seconds ---
--- 0.0 entropy seconds ---
--- 0.0 sharpness seconds ---
--- 0.0009982585906982422 degree seconds ---
--- 0.0 homoginity seconds ---
--- 0.0 mean seconds ---
--- 0.0 var seconds ---
--- 0.0 energy seconds ---
--- 0.0 entropy seconds ---
--- 0.0 sharpness seconds ---
--- 0.0 degree seconds ---
--- 0.0 homoginity seconds ---
--- 0.0 mean seconds ---
--- 0.0 var seconds ---
--- 0.0 energy seconds ---
--- 0.0 entropy seconds ---
--- 0.0 sharpness seconds ---
--- 0.0 degree seconds ---
--- 0.0 homoginity seconds ---
--- 0.0 mean seconds ---
--- 0.0 var seconds ---
--- 0.0 energy seconds ---
--- 0.0 entropy seconds ---
--- 0.0 sharpness seconds ---
--- 0.0009970664978027344 degree secon

In [35]:
train_data[0].shape

(64, 1050, 1)

In [60]:
import time
start_time = time.time()
train_data = next(train_datagen)
print("--- %s seconds ---" % (time.time() - start_time))

--- 0.0 DWT seconds ---
--- 0.0 mean seconds ---
--- 0.0 var seconds ---
--- 0.0 energy seconds ---
--- 0.0 entropy seconds ---
--- 0.0 sharpness seconds ---
--- 0.0 degree seconds ---
--- 0.0 homoginity seconds ---
--- 0.0 mean seconds ---
--- 0.0 var seconds ---
--- 0.0 energy seconds ---
--- 0.0 entropy seconds ---
--- 0.000997781753540039 sharpness seconds ---
--- 0.0 degree seconds ---
--- 0.0 homoginity seconds ---
--- 0.0 mean seconds ---
--- 0.0 var seconds ---
--- 0.0 energy seconds ---
--- 0.0 entropy seconds ---
--- 0.0 sharpness seconds ---
--- 0.0 degree seconds ---
--- 0.0 homoginity seconds ---
--- 0.0 mean seconds ---
--- 0.0 var seconds ---
--- 0.0 energy seconds ---
--- 0.0 entropy seconds ---
--- 0.0 sharpness seconds ---
--- 0.0 degree seconds ---
--- 0.0 homoginity seconds ---
--- 0.0 mean seconds ---
--- 0.0 var seconds ---
--- 0.0 energy seconds ---
--- 0.0 entropy seconds ---
--- 0.0 sharpness seconds ---
--- 0.0 degree seconds ---
--- 0.0 homoginity seconds ---

--- 0.0009975433349609375 homoginity seconds ---
--- 0.012965679168701172 total extraction per wavelet seconds ---
--- 0.001996755599975586 DWT seconds ---
--- 0.0 mean seconds ---
--- 0.0 var seconds ---
--- 0.0 energy seconds ---
--- 0.0 entropy seconds ---
--- 0.0 sharpness seconds ---
--- 0.0 degree seconds ---
--- 0.0 homoginity seconds ---
--- 0.0 mean seconds ---
--- 0.0 var seconds ---
--- 0.0 energy seconds ---
--- 0.0 entropy seconds ---
--- 0.0 sharpness seconds ---
--- 0.0 degree seconds ---
--- 0.0 homoginity seconds ---
--- 0.0 mean seconds ---
--- 0.0 var seconds ---
--- 0.0 energy seconds ---
--- 0.0 entropy seconds ---
--- 0.0 sharpness seconds ---
--- 0.0 degree seconds ---
--- 0.0 homoginity seconds ---
--- 0.0 mean seconds ---
--- 0.0 var seconds ---
--- 0.0 energy seconds ---
--- 0.0 entropy seconds ---
--- 0.0 sharpness seconds ---
--- 0.0010256767272949219 degree seconds ---
--- 0.0 homoginity seconds ---
--- 0.0 mean seconds ---
--- 0.0 var seconds ---
--- 0.0 e

--- 0.0009970664978027344 homoginity seconds ---
--- 0.0 mean seconds ---
--- 0.0 var seconds ---
--- 0.0 energy seconds ---
--- 0.0 entropy seconds ---
--- 0.0009989738464355469 sharpness seconds ---
--- 0.0 degree seconds ---
--- 0.0009975433349609375 homoginity seconds ---
--- 0.01595759391784668 total extraction per wavelet seconds ---
--- 0.0019676685333251953 DWT seconds ---
--- 0.0 mean seconds ---
--- 0.0 var seconds ---
--- 0.0 energy seconds ---
--- 0.0 entropy seconds ---
--- 0.0 sharpness seconds ---
--- 0.0 degree seconds ---
--- 0.0 homoginity seconds ---
--- 0.0 mean seconds ---
--- 0.0 var seconds ---
--- 0.0 energy seconds ---
--- 0.0 entropy seconds ---
--- 0.0009942054748535156 sharpness seconds ---
--- 0.0 degree seconds ---
--- 0.0 homoginity seconds ---
--- 0.0 mean seconds ---
--- 0.0 var seconds ---
--- 0.0 energy seconds ---
--- 0.0 entropy seconds ---
--- 0.0 sharpness seconds ---
--- 0.0 degree seconds ---
--- 0.000997304916381836 homoginity seconds ---
--- 0

--- 0.000997304916381836 degree seconds ---
--- 0.0009975433349609375 homoginity seconds ---
--- 0.0 mean seconds ---
--- 0.0 var seconds ---
--- 0.0 energy seconds ---
--- 0.0 entropy seconds ---
--- 0.0009968280792236328 sharpness seconds ---
--- 0.0009975433349609375 degree seconds ---
--- 0.0009975433349609375 homoginity seconds ---
--- 0.017945528030395508 total extraction per wavelet seconds ---
--- 0.0 DWT seconds ---
--- 0.0 mean seconds ---
--- 0.0 var seconds ---
--- 0.0 energy seconds ---
--- 0.0 entropy seconds ---
--- 0.0 sharpness seconds ---
--- 0.0 degree seconds ---
--- 0.0 homoginity seconds ---
--- 0.0 mean seconds ---
--- 0.0 var seconds ---
--- 0.0 energy seconds ---
--- 0.0 entropy seconds ---
--- 0.0 sharpness seconds ---
--- 0.0 degree seconds ---
--- 0.0009999275207519531 homoginity seconds ---
--- 0.0 mean seconds ---
--- 0.0 var seconds ---
--- 0.0 energy seconds ---
--- 0.0 entropy seconds ---
--- 0.0 sharpness seconds ---
--- 0.0 degree seconds ---
--- 0.0 

--- 0.000997781753540039 homoginity seconds ---
--- 0.0 mean seconds ---
--- 0.0 var seconds ---
--- 0.0 energy seconds ---
--- 0.0 entropy seconds ---
--- 0.0009963512420654297 sharpness seconds ---
--- 0.0009946823120117188 degree seconds ---
--- 0.001001119613647461 homoginity seconds ---
--- 0.0 mean seconds ---
--- 0.0 var seconds ---
--- 0.0 energy seconds ---
--- 0.0 entropy seconds ---
--- 0.000997304916381836 sharpness seconds ---
--- 0.0 degree seconds ---
--- 0.0009970664978027344 homoginity seconds ---
--- 0.0 mean seconds ---
--- 0.0009965896606445312 var seconds ---
--- 0.0 energy seconds ---
--- 0.0 entropy seconds ---
--- 0.000997304916381836 sharpness seconds ---
--- 0.0 degree seconds ---
--- 0.0010106563568115234 homoginity seconds ---
--- 0.014960765838623047 total extraction per wavelet seconds ---
--- 0.000993967056274414 DWT seconds ---
--- 0.0 mean seconds ---
--- 0.0 var seconds ---
--- 0.0 energy seconds ---
--- 0.0 entropy seconds ---
--- 0.0 sharpness second

...

--- 0.0010247230529785156 homoginity seconds ---
--- 0.0 mean seconds ---
--- 0.0 var seconds ---
--- 0.0 energy seconds ---
--- 0.0 entropy seconds ---
--- 0.0 sharpness seconds ---
--- 0.0 degree seconds ---
--- 0.0 homoginity seconds ---
--- 0.0 mean seconds ---
--- 0.0 var seconds ---
--- 0.0 energy seconds ---
--- 0.0 entropy seconds ---
--- 0.0 sharpness seconds ---
--- 0.0 degree seconds ---
--- 0.0009965896606445312 homoginity seconds ---
--- 0.0 mean seconds ---
--- 0.0 var seconds ---
--- 0.0 energy seconds ---
--- 0.0 entropy seconds ---
--- 0.0 sharpness seconds ---
--- 0.000997304916381836 degree seconds ---
--- 0.0 homoginity seconds ---
--- 0.0 mean seconds ---
--- 0.0 var seconds ---
--- 0.0 energy seconds ---
--- 0.0 entropy seconds ---
--- 0.0009965896606445312 sharpness seconds ---
--- 0.0 degree seconds ---
--- 0.0 homoginity seconds ---
--- 0.0 mean seconds ---
--- 0.0 var seconds ---
--- 0.0 energy seconds ---
--- 0.0009708404541015625 entropy seconds ---
--- 0.00

--- 0.001001596450805664 homoginity seconds ---
--- 0.0 mean seconds ---
--- 0.0 var seconds ---
--- 0.0 energy seconds ---
--- 0.0 entropy seconds ---
--- 0.0009932518005371094 sharpness seconds ---
--- 0.0010001659393310547 degree seconds ---
--- 0.0009949207305908203 homoginity seconds ---
--- 0.0 mean seconds ---
--- 0.0 var seconds ---
--- 0.0 energy seconds ---
--- 0.0 entropy seconds ---
--- 0.0010018348693847656 sharpness seconds ---
--- 0.000965118408203125 degree seconds ---
--- 0.0010259151458740234 homoginity seconds ---
--- 0.013964414596557617 total extraction per wavelet seconds ---
--- 0.0009958744049072266 DWT seconds ---
--- 0.0 mean seconds ---
--- 0.0 var seconds ---
--- 0.0 energy seconds ---
--- 0.0 entropy seconds ---
--- 0.0 sharpness seconds ---
--- 0.0 degree seconds ---
--- 0.0 homoginity seconds ---
--- 0.0 mean seconds ---
--- 0.0 var seconds ---
--- 0.0 energy seconds ---
--- 0.0 entropy seconds ---
--- 0.0 sharpness seconds ---
--- 0.0009703636169433594 d

--- 0.0009982585906982422 DWT seconds ---
--- 0.0 mean seconds ---
--- 0.0 var seconds ---
--- 0.0 energy seconds ---
--- 0.0 entropy seconds ---
--- 0.0 sharpness seconds ---
--- 0.0009944438934326172 degree seconds ---
--- 0.0 homoginity seconds ---
--- 0.0 mean seconds ---
--- 0.0 var seconds ---
--- 0.0 energy seconds ---
--- 0.0 entropy seconds ---
--- 0.0 sharpness seconds ---
--- 0.0 degree seconds ---
--- 0.0 homoginity seconds ---
--- 0.0 mean seconds ---
--- 0.0 var seconds ---
--- 0.0 energy seconds ---
--- 0.0 entropy seconds ---
--- 0.0009698867797851562 sharpness seconds ---
--- 0.0 degree seconds ---
--- 0.0 homoginity seconds ---
--- 0.0 mean seconds ---
--- 0.0 var seconds ---
--- 0.0 energy seconds ---
--- 0.0 entropy seconds ---
--- 0.0 sharpness seconds ---
--- 0.0 degree seconds ---
--- 0.001024007797241211 homoginity seconds ---
--- 0.0 mean seconds ---
--- 0.0 var seconds ---
--- 0.0 energy seconds ---
--- 0.0 entropy seconds ---
--- 0.0 sharpness seconds ---
---

--- 0.000997781753540039 degree seconds ---
--- 0.0009698867797851562 homoginity seconds ---
--- 0.0 mean seconds ---
--- 0.0 var seconds ---
--- 0.0 energy seconds ---
--- 0.0 entropy seconds ---
--- 0.0010242462158203125 sharpness seconds ---
--- 0.0009996891021728516 degree seconds ---
--- 0.000995635986328125 homoginity seconds ---
--- 0.0 mean seconds ---
--- 0.0 var seconds ---
--- 0.0 energy seconds ---
--- 0.0 entropy seconds ---
--- 0.0009975433349609375 sharpness seconds ---
--- 0.0009965896606445312 degree seconds ---
--- 0.00099945068359375 homoginity seconds ---
--- 0.0 mean seconds ---
--- 0.0 var seconds ---
--- 0.0 energy seconds ---
--- 0.0 entropy seconds ---
--- 0.0009961128234863281 sharpness seconds ---
--- 0.0009958744049072266 degree seconds ---
--- 0.0009975433349609375 homoginity seconds ---
--- 0.017951250076293945 total extraction per wavelet seconds ---
--- 0.0010004043579101562 DWT seconds ---
--- 0.0 mean seconds ---
--- 0.0 var seconds ---
--- 0.0 energy 

--- 0.000997781753540039 DWT seconds ---
--- 0.0 mean seconds ---
--- 0.0 var seconds ---
--- 0.0 energy seconds ---
--- 0.0 entropy seconds ---
--- 0.0 sharpness seconds ---
--- 0.0 degree seconds ---
--- 0.0 homoginity seconds ---
--- 0.0 mean seconds ---
--- 0.0 var seconds ---
--- 0.0 energy seconds ---
--- 0.0 entropy seconds ---
--- 0.0 sharpness seconds ---
--- 0.0 degree seconds ---
--- 0.0 homoginity seconds ---
--- 0.0 mean seconds ---
--- 0.0 var seconds ---
--- 0.0 energy seconds ---
--- 0.0 entropy seconds ---
--- 0.0 sharpness seconds ---
--- 0.0 degree seconds ---
--- 0.0 homoginity seconds ---
--- 0.0 mean seconds ---
--- 0.0 var seconds ---
--- 0.0 energy seconds ---
--- 0.0 entropy seconds ---
--- 0.0 sharpness seconds ---
--- 0.0 degree seconds ---
--- 0.0009944438934326172 homoginity seconds ---
--- 0.0 mean seconds ---
--- 0.0 var seconds ---
--- 0.0 energy seconds ---
--- 0.0 entropy seconds ---
--- 0.0 sharpness seconds ---
--- 0.0 degree seconds ---
--- 0.0 homo

In [37]:
train_data[0].shape

(64, 1050, 1)

In [39]:
print(len(os.listdir('../input/patches/train/pristine/')))
print(len(os.listdir('../input/patches/train/fake/')))

2308359
1442732


In [40]:
2308359 + 1442732

3751091

In [63]:
from concurrent.futures import ProcessPoolExecutor

In [64]:
from time import sleep
def task(message):
    sleep(2)
    return message

In [73]:
nums =  ['1', '2', '3', '4', '5']

In [74]:
with ProcessPoolExecutor() as executor:
        print([val for val in executor.map(task, nums)])

BrokenProcessPool: A process in the process pool was terminated abruptly while the future was running or pending.